In [1]:
import pandas as pd

import json
from pandas.io.json import json_normalize

from IPython.display import IFrame

# Datengui.de Praxis @SciCar

Disclaimer: 

Datengui.de befindet sich in der Entwicklung. 
Es gibt eine API und erste Prototypen, um die API zu benutzen. 
Die eigentliche Anwendung ist aber noch nicht da. 
Deswegen ist der hier beschriebene Weg etwas umständlich und beeinhaltet technische Hürden. 
Trotzdem wollten wir Euch die API schon einmal ausprobieren lassen, denn jeder Hinweis von Euch hilft, um die API in der späteren Anwendung besser nutzbar zu machen. Und falls ihr die Hürden nehmt, könnt ihr die Daten schon nutzen :)

## Schritt 1: Datensatz suchen

Simon Wörpel hat dazu folgende Flask App gebaut: 
**[Regionalstatistik: docs.genesapi.org](https://docs.genesapi.org)**

Sucht doch mal zum Beispiel nach 'Kühe' 

Ergebnis:
    
**https://docs.genesapi.org/AI0902**

Runterscrollen bis zum [**Beispiel**](https://api-next.datengui.de/graphql?query=%7B%0A%20%20allRegions%20%7B%0A%20%20%20%20page%0A%20%20%20%20total%0A%20%20%20%20itemsPerPage%0A%20%20%20%20regions%20%7B%0A%20%20%20%20%20%20id%0A%20%20%20%20%20%20name%0A%20%20%20%20%20%20AI0902%20%7B%0A%20%20%20%20%20%20%20%20year%0A%20%20%20%20%20%20%20%20value%0A%20%20%20%20%20%20%7D%0A%20%20%20%20%7D%0A%20%20%7D%0A%7D%0A)

Dieser Link führt zu: 
    [**Datenguide API Playground - alpha**](https://api-next.datengui.de/graphql)

Auf ▶️ Play-Drücken:
    
Daten werden abgerufen und rechts angezeigt.

**Was könnt und solltet ihr anpassen:** 

- `itemsPerPage`: Wie viele Elemente enthält der Datensatz
    
- `nuts`: Das ist die lustige, aber offizielle EU-weite Bezeichnung für Gebiets-Ebenen. Nicht alle Daten sind auf allen Gebiets-Ebenen verfügbar.
    - `nuts: 1` steht für die Ebene Bundesländer
    - `nuts: 3` steht für die Ebene Kreise und kreisfreie Städte
    - Statt `nuts` könnt ihr auch `lau: 1` benutzen, um Daten auf Gemeinde-Ebene abzufragen.
    
    
Einschränken der Datenabfrage mittels Filter:
    
Ihr könnt in Klammern hinter dem Merkmal (`AI0902`) noch Filter setzen:
    
- `year`: Zeitpunkt der Daten einschränken, zum Beispiel `year: 2016`, um nur Daten für 2016 zu zeigen. Aktuell sind in unserer (experimentellen) API Daten bis 2017 enthalten.
- *Ausprägungen des Merkmals:*
  Viele Merkmale haben noch verschiedene Ausprägungen. Zum Beispiel [Bevölkerungsstand](https://docs.genesapi.org/BEVSTD) – hier könnt ihr die Abfrage durch Attribute eingränzen, zum Beispiel nur Daten für das weibliche Geschlecht abfragen ([Beispiel](https://docs.genesapi.org/BEVSTD/GES))

## Schritt 2: Daten speichern

Rechte Seite komplett markieren und als `kuehe.json` speichern

### Alternative für Experten: Daten direkt in dieses Notebook laden

Ihr könnt mit der `requests`-Library ganz einfach auch die Antwort der API-Abfrage direkt laden:

In [ ]:
import requests

url = 'https://api-next.datengui.de/graphql'

query = """
{
  allRegions (itemsPerPage: 50) {
    page
    total
    itemsPerPage
    regions (nuts: 1) {
      id
      name
      AI0902 (year: 2016) {
        year
        value
      }
    }
  }
}
"""

res = requests.post(url, data={'query': query})
d = res.json()  # das weiter unten nutzen anstatt es aus der Datei (nächster Schritt) zu laden

## Schritt 3: .json einlesen

In Zukunft soll das Ganze natürlich in verschiedenen Formaten (zum Beispiel .csv) herunterladbar sein.
Gregor Aisch hat da mal einen Prototypen gebaut: https://gka.me/datenguide/. Rückmeldungen, Wünsche dazu gerne. 

Hier kommt der Python-Weg:

In [3]:
#load json object
with open('kuehe.json') as f:
    d = json.load(f)

In [4]:
d

{'data': {'allRegions': {'page': 0,
   'total': 16,
   'itemsPerPage': 50,
   'regions': [{'id': '10',
     'name': 'Saarland',
     'AI0902': [{'year': 2016, 'value': 61.7}]},
    {'id': '11', 'name': 'Berlin', 'AI0902': [{'year': 2016, 'value': 23.6}]},
    {'id': '12',
     'name': 'Brandenburg',
     'AI0902': [{'year': 2016, 'value': 40.4}]},
    {'id': '13',
     'name': 'Mecklenburg-Vorpommern',
     'AI0902': [{'year': 2016, 'value': 40.6}]},
    {'id': '14', 'name': 'Sachsen', 'AI0902': [{'year': 2016, 'value': 53.7}]},
    {'id': '15',
     'name': 'Sachsen-Anhalt',
     'AI0902': [{'year': 2016, 'value': 28.6}]},
    {'id': '16',
     'name': 'Thüringen',
     'AI0902': [{'year': 2016, 'value': 41.5}]},
    {'id': '01',
     'name': 'Schleswig-Holstein',
     'AI0902': [{'year': 2016, 'value': 110.7}]},
    {'id': '02', 'name': 'Hamburg', 'AI0902': [{'year': 2016, 'value': 42.1}]},
    {'id': '03',
     'name': 'Niedersachsen',
     'AI0902': [{'year': 2016, 'value': 100.3}]

In [5]:
d = d['data']['allRegions']['regions']

In [6]:
d

[{'id': '10', 'name': 'Saarland', 'AI0902': [{'year': 2016, 'value': 61.7}]},
 {'id': '11', 'name': 'Berlin', 'AI0902': [{'year': 2016, 'value': 23.6}]},
 {'id': '12',
  'name': 'Brandenburg',
  'AI0902': [{'year': 2016, 'value': 40.4}]},
 {'id': '13',
  'name': 'Mecklenburg-Vorpommern',
  'AI0902': [{'year': 2016, 'value': 40.6}]},
 {'id': '14', 'name': 'Sachsen', 'AI0902': [{'year': 2016, 'value': 53.7}]},
 {'id': '15',
  'name': 'Sachsen-Anhalt',
  'AI0902': [{'year': 2016, 'value': 28.6}]},
 {'id': '16', 'name': 'Thüringen', 'AI0902': [{'year': 2016, 'value': 41.5}]},
 {'id': '01',
  'name': 'Schleswig-Holstein',
  'AI0902': [{'year': 2016, 'value': 110.7}]},
 {'id': '02', 'name': 'Hamburg', 'AI0902': [{'year': 2016, 'value': 42.1}]},
 {'id': '03',
  'name': 'Niedersachsen',
  'AI0902': [{'year': 2016, 'value': 100.3}]},
 {'id': '04', 'name': 'Bremen', 'AI0902': [{'year': 2016, 'value': 124.1}]},
 {'id': '05',
  'name': 'Nordrhein-Westfalen',
  'AI0902': [{'year': 2016, 'value': 98

In [7]:
d = json_normalize(d, 'AI0902', ['id', 'name', ['year', 'value']], errors='ignore')

In [8]:
d

year  value  id                    name year.value
0   2016   61.7  10                Saarland        NaN
1   2016   23.6  11                  Berlin        NaN
2   2016   40.4  12             Brandenburg        NaN
3   2016   40.6  13  Mecklenburg-Vorpommern        NaN
4   2016   53.7  14                 Sachsen        NaN
5   2016   28.6  15          Sachsen-Anhalt        NaN
6   2016   41.5  16               Thüringen        NaN
7   2016  110.7  01      Schleswig-Holstein        NaN
8   2016   42.1  02                 Hamburg        NaN
9   2016  100.3  03           Niedersachsen        NaN
10  2016  124.1  04                  Bremen        NaN
11  2016   98.1  05     Nordrhein-Westfalen        NaN
12  2016   57.2  06                  Hessen        NaN
13  2016   49.1  07         Rheinland-Pfalz        NaN
14  2016   69.5  08       Baden-Württemberg        NaN
15  2016  101.9  09                  Bayern        NaN

In [9]:
d = d[['value', 'name']]

In [10]:
d

value                    name
0    61.7                Saarland
1    23.6                  Berlin
2    40.4             Brandenburg
3    40.6  Mecklenburg-Vorpommern
4    53.7                 Sachsen
5    28.6          Sachsen-Anhalt
6    41.5               Thüringen
7   110.7      Schleswig-Holstein
8    42.1                 Hamburg
9   100.3           Niedersachsen
10  124.1                  Bremen
11   98.1     Nordrhein-Westfalen
12   57.2                  Hessen
13   49.1         Rheinland-Pfalz
14   69.5       Baden-Württemberg
15  101.9                  Bayern

In [11]:
d = d.set_index('name')

In [12]:
d

value
name                         
Saarland                 61.7
Berlin                   23.6
Brandenburg              40.4
Mecklenburg-Vorpommern   40.6
Sachsen                  53.7
Sachsen-Anhalt           28.6
Thüringen                41.5
Schleswig-Holstein      110.7
Hamburg                  42.1
Niedersachsen           100.3
Bremen                  124.1
Nordrhein-Westfalen      98.1
Hessen                   57.2
Rheinland-Pfalz          49.1
Baden-Württemberg        69.5
Bayern                  101.9

In [13]:
# d.to_clipboard()
d.to_csv('kuehe.csv')

## Schritt 4: Datawrapper

- Neue Karte
- Deutschland: Bundesländer 
- Daten einfügen
- Anpassen

In [14]:
IFrame('//datawrapper.dwcdn.net/AWDSM/2/', width='600', height='400')